#Additional Attacks Experiments

## Link Google Drive for pretrained models

In [1]:
from google.colab import drive
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


##Install/import Dependencies

In [2]:
import torch

In [3]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [4]:
!pip install sacremoses

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [5]:
!pip install textattack


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [6]:
!pip install validators

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [7]:
!pip install tldextract

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [8]:
!pip install rfc3986

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [9]:
from rfc3986 import is_valid_uri
import validators
import tldextract

In [10]:
!pip install tensorflow_text

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached importlib_metadata-4.12.0-py3-none-any.whl (21 kB)
  Attempting uninstall: importlib-metadata
    Found existing installation: importlib-metadata 3.10.1
    Uninstalling importlib-metadata-3.10.1:
      Successfully uninstalled importlib-metadata-3.10.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
konoha 4.6.5 requires importlib-metadata<4.0.0,>=3.7.0, but you have importlib-metadata 4.12.0 which is incompatible.


In [11]:
import torch
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [12]:
!pip install Flair

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached importlib_metadata-3.10.1-py3-none-any.whl (14 kB)
  Attempting uninstall: importlib-metadata
    Found existing installation: importlib-metadata 4.12.0
    Uninstalling importlib-metadata-4.12.0:
      Successfully uninstalled importlib-metadata-4.12.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
markdown 3.4.1 requires importlib-metadata>=4.4; python_version < "3.10", but you have importlib-metadata 3.10.1 which is incompatible.
gym 0.25.1 requires importlib-metadata>=4.8.0; python_version < "3.10", but you have importlib-metadata 3.10.1 which is incompatible.


#TEST-SEEDURLS-POPULAR-BASE (NOT CRAWLED)

In [24]:
import pandas as pd
def test_data():
  
  test_data=pd.read_csv(path+'popularseedurlsbase.csv',encoding="utf-8")
  data_test=test_data['url']
  test_labels=list(test_data['label'])
  # add special tokens for BERT to work properly
  test_data_preprocessed = [(i, query,test_labels[i]) for i, query in enumerate(data_test)]
  return test_data_preprocessed

#ATTACK ON PRETRAINED EXPOSE MODEL

In [ ]:
from keras.preprocessing import sequence
from keras.models import Sequential, Model
from keras.layers.core import Dense, Dropout, Activation, Flatten, Lambda
from tensorflow.keras.layers import LSTM, GRU, SimpleRNN
from keras.layers import Concatenate
from keras.layers.convolutional import Convolution1D, MaxPooling1D
from tensorflow.keras.layers import BatchNormalization
from tensorflow.keras.layers import PReLU
from keras.layers import Input, Embedding, LSTM
from keras.models import Model
from keras.datasets import imdb
from keras.callbacks import ModelCheckpoint
from keras import backend as K
from keras.regularizers import l2, l1
from keras.callbacks import EarlyStopping
from collections import defaultdict as ddict
from sklearn.ensemble import RandomForestClassifier as RF
from sklearn.metrics import matthews_corrcoef,f1_score,precision_score,recall_score,roc_auc_score,auc,confusion_matrix

from numpy import *
import json
import pandas as pd
import csv
from sklearn.utils import shuffle
import numpy as np
def sum_1d(X):
    return K.sum(X, axis=1)

def getconvmodel(filter_length,nb_filter):
    model = Sequential()
    model.add(Convolution1D(nb_filter=nb_filter,
                            input_shape=(100,32),
                            filter_length=filter_length,
                            border_mode='same',
                            activation='relu',
                            subsample_length=1))
    model.add(Lambda(sum_1d, output_shape=(nb_filter,)))
    #model.add(BatchNormalization(mode=0))
    model.add(Dropout(0.5))
    return model

def mlp_model(optimizer="adam"):
    main_input = Input(shape=(1024,), dtype='float32', name='main_input')

    middle = Dense(1024,activation='relu')(main_input)
    middle = Dropout(0.5)(middle)
    middle = BatchNormalization()(middle)

    middle = Dense(1024,activation='relu')(main_input)
    middle = Dropout(0.5)(middle)
    middle = BatchNormalization()(middle)

    output = Dense(1,activation='sigmoid')(middle)

    model = Model(input=main_input,output=output)
    model.compile(loss='binary_crossentropy', optimizer=optimizer)
    return model

def bag_of_convs_model(optimizer="adam",compile=True):
    main_input = Input(shape=(100,), dtype='int32', name='main_input')
    embedding = Embedding(output_dim=32, input_dim=100, input_length=100,
        dropout=0)(main_input)

    conv1 = getconvmodel(2,256)(embedding)
    conv2 = getconvmodel(3,256)(embedding)
    conv3 = getconvmodel(4,256)(embedding)
    conv4 = getconvmodel(5,256)(embedding)

    merged = Concatenate()([conv1,conv2,conv3,conv4])

    middle = Dense(1024,activation='relu')(merged)
    middle = Dropout(0.5)(middle)

    middle = Dense(1024,activation='relu')(middle)
    middle = Dropout(0.5)(middle)

    output = Dense(1,activation='sigmoid')(middle)

    model = Model(input=main_input,output=output)
    if compile:
        model.compile(loss='binary_crossentropy', optimizer=optimizer)
    return model

def randomforest():
    rf = RF(256,verbose=True,n_jobs=50)
    return rf




In [ ]:
import os
os.chdir(f'/content/gdrive/My Drive/TDSC_Additional_Experiments/eXposeDeepNeuralNetwork-master/src')

In [ ]:
import os
import numpy
from modeling import features
from keras.models import model_from_json
from tensorflow.keras import backend as K
from keras.models import load_model
#!/usr/bin/python


In [ ]:
from textattack.models.wrappers import ModelWrapper
class CustomTokenizer:
    
    def __init__(self,model_type,filename):
           self.model_type=model_type
           self.filename=filename+'tried.csv'
    def encode(self, strings):
        fvecs = []
        for string in strings:
            if self.model_type in ('rf','mlp'):
                fvecs.append(features.ngrams_extract(string))
            elif self.model_type == 'convnet':
                fvecs.append(features.sequence(string))
                adv=open(self.filename, 'a+' ,encoding='utf-8',newline='')
                ad= csv.writer(adv)
                ad.writerow([string])
                adv.close()
               


                
            else:
                raise Exception("unknown model type")
        return numpy.array(fvecs)

class CustomTensorFlowModelWrapper(ModelWrapper):
    def __init__(self,model_type,filename):
        self.model_type=model_type
        self.tokenizer=CustomTokenizer(model_type,filename)
        self.model = model_from_json(open('/content/gdrive/My Drive/TDSC_Additional_Experiments/eXposeDeepNeuralNetwork-master/model_def.json').read(),custom_objects={"K": K})
        self.model.load_weights('/content/gdrive/My Drive/TDSC_Additional_Experiments/eXposeDeepNeuralNetwork-master/model_weights.h5')
        self.model.compile(optimizer='adam', loss='binary_crossentropy')
              
    def __call__(self, testurls):
        """
        Score a list of strings, returning a list [[string,score],...]
        """
        
        input_data = self.tokenizer.encode(testurls)
        if self.model_type == 'rf':
            result = (self.model.predict_probas(input_data)[:,-1])
        elif self.model_type in ('mlp','convnet'):
            result =self.model.predict(input_data)
            predictions=[]
            for i in range(len(testurls)): 
                predlabel=[0,0]
                if(result[i]>=0.5):
                  predlabel[1]=float(result[i])
                  predlabel[0]=float(1-result[i])
                else:
                  predlabel[1]=float(result[i])
                  predlabel[0]=float(1-result[i])
                # print(testurls[i],"  ",predlabel)
                predictions.append(np.array(predlabel))

           
            return predictions
        


textattack: Updating TextAttack package dependencies.
textattack: Downloading NLTK required packages.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package omw to /root/nltk_data...
[nltk_data] Downloading package universal_tagset to /root/nltk_data...
[nltk_data]   Unzipping taggers/universal_tagset.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


###TEXTATTACK ATTACKS

In [ ]:
import textattack
import codecs,tldextract
codecs.register_error("strict", codecs.ignore_errors)
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'DeepWordBug_Expose_1.csv'
model = CustomTensorFlowModelWrapper('convnet',filename)
tokenizer=CustomTokenizer('convnet',filename)
attack = textattack.attack_recipes.DeepWordBugGao2018.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1/1 [==============================] - 0s 15ms/step
['0', 'http://ir.netflix.com/', '0.05835461616516113', '0', 'httm://ir.netflix.co/', '0.9680077433586121', '1', 'SUCCESS', 'False', 'False', 'True']
1/1 [==============================] - 0s 15ms/step
['1', 'http://netflix.com', '0.05860787630081177', '0', 'httP://netflix.com', '0.9471450448036194', '1', 'SUCCESS', 'True', 'False', 'False']
1/1 [==============================] - 0s 14ms/step
['2', 'http://netflix.com/', '0.4193459749221802', '0', 'Ehttp://netflix.com/', '0.9967148303985596', '1', 'SUCCESS', 'False', 'False', 'False']
1/1 [==============================] - 0s 14ms/step
['3', 'http://netflix.com/au/', '0.9977253079414368', '1', 'http://netflix.com/au/', '0.9977253079414368', '1', 'SKIPPED', 'True', 'False', 'False']
1/1 [==============================] - 0s 15ms/step
['4', 'http://netflix.com/login', '0.9997606873512268', '1', 'http://netflix.com/login', '0.9997606873512268', '1', 'SKIPPED', 'True', 'False', 'False']
1/

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'Pruthi2019_Expose.csv'
model = CustomTensorFlowModelWrapper('convnet',filename)
tokenizer=CustomTokenizer('convnet',filename)
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.Pruthi2019.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1/1 [==============================] - 0s 16ms/step
['0', 'http://ir.netflix.com/', '0.05835461616516113', '0', 'hYttp://ir.netflix.com/', '0.9974660873413086', '1', 'SUCCESS', 'False', 'False', 'False']
1/1 [==============================] - 0s 60ms/step
['1', 'http://netflix.com', '0.05860787630081177', '0', 'http://netfSlix.com', '0.9911746978759766', '1', 'SUCCESS', 'True', 'True', 'False']
1/1 [==============================] - 0s 16ms/step
['2', 'http://netflix.com/', '0.4193459749221802', '0', 'http://netflJix.com/', '0.9953150749206543', '1', 'SUCCESS', 'True', 'True', 'False']
1/1 [==============================] - 0s 14ms/step
['3', 'http://netflix.com/au/', '0.9977253079414368', '1', 'http://netflix.com/au/', '0.9977253079414368', '1', 'SKIPPED', 'True', 'False', 'False']
1/1 [==============================] - 0s 16ms/step
['4', 'http://netflix.com/login', '0.9997606873512268', '1', 'http://netflix.com/login', '0.9997606873512268', '1', 'SKIPPED', 'True', 'False', 'False']
1

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'PWWS_Expose.csv'
model = CustomTensorFlowModelWrapper('convnet',filename)
tokenizer=CustomTokenizer('convnet',filename)
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.PWWSRen2019.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid]
          print(row)
          ad.writerow(row)
adv.close()

[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1/1 [==============================] - 0s 17ms/step
['0', 'http://ir.netflix.com/', '0.05835461616516113', '0', 'http://Ir.netflix.com/', '0.9999271631240845', '1', 'SUCCESS', 'True', 'False', 'False']
1/1 [==============================] - 0s 26ms/step
['1', 'http://netflix.com', '0.05860787630081177', '0', 'HTTP://netflix.com', '0.9998207688331604', '1', 'SUCCESS', 'True', 'False', 'False']
1/1 [==============================] - 0s 18ms/step
['2', 'http://netflix.com/', '0.4193459749221802', '0', 'HTTP://netflix.com/', '0.9999289512634277', '1', 'SUCCESS', 'True', 'False', 'False']
1/1 [==============================] - 0s 16ms/step
['3', 'http://netflix.com/au/', '0.9977253079414368', '1', 'http://netflix.com/au/', '0.9977253079414368', '1', 'SKIPPED', 'True', 'False', 'False']
1/1 [==============================] - 0s 24ms/step
['4', 'http://netflix.com/login', '0.9997606873512268', '1', 'http://netflix.com/login', '0.9997606873512268', '1', 'SKIPPED', 'True', 'False', 'False']
1/1

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'TEXTBUGGER_Expose.csv'
model = CustomTensorFlowModelWrapper('convnet',filename)
tokenizer=CustomTokenizer('convnet',filename)
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.TextBuggerLi2018.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid]
          print(row)
          ad.writerow(row)
adv.close()

#URLNET

In [1]:
import os
os.chdir(f'/content/gdrive/My Drive/TDSC_Additional_Experiments/URLNet-master/')

# New Section

In [14]:
!pip install tflearn

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [3]:
import tensorflow as tf 
tf.compat.v1.disable_v2_behavior()
tf.compat.v1.enable_eager_execution()

Instructions for updating:
non-resource variables are not supported in the long term


In [7]:
tf.compat.v1.executing_eagerly()

False

In [5]:
import pickle 
import time 
import numpy as np 
import pickle 
import pandas as pd
import csv
from sklearn.utils import shuffle
from rfc3986 import is_valid_uri
import validators
import tldextract
from utils import *
from tflearn.data_utils import to_categorical, pad_sequences
from tqdm import tqdm
import argparse

In [8]:
# -*- coding: utf-8 -*-
"""
Created on Thu Aug 18 13:23:01 2022

@author: bushra
"""

#tf.compat.v1.disable_v2_behavior()
from textattack.models.wrappers import ModelWrapper

def softmax(x): 
    e_x = np.exp(x - np.max(x))
    return e_x / e_x.sum() 
######################## EVALUATION ########################### 
class CustomTensorFlowModelWrapperURLNET(ModelWrapper):
  def __init__(self,configuration):
    self.outputdir="/content/gdrive/My Drive/TDSC_Additional_Experiments/URLNet-master/runs/10000/"+str(configuration)+"/"
    self.max_len_words = 200
    self.max_len_chars = 200
    self.max_len_subwords = 20
    self.data_dir='train_10000.txt'
    self.delimit_mode=1
    self.subword_dict_dir=self.outputdir+"subwords_dict.p"
    self.word_dict_dir=self.outputdir+"words_dict.p"
    self.char_dict_dir=self.outputdir+"chars_dict.p"
    # model args 
    self.emb_dim = 32
    self.emb_mode = configuration 
    #help="1: charCNN, 2: wordCNN, 3: char + wordCNN, 4: char-level wordCNN, 5: char + char-level wordCNN (default: {})".format(default_emb_mode))
    self.batch_size = 128
    self.checkpoint_dir=self.outputdir+"checkpoints/"
    self.checkpoint_file = tf.compat.v1.train.latest_checkpoint(self.checkpoint_dir)
    
    self.graph = tf.compat.v1.Graph() 
    with self.graph.as_default(): 
                session_conf = tf.compat.v1.ConfigProto(allow_soft_placement=True, log_device_placement=False)
                session_conf.gpu_options.allow_growth=True 
                self.model = tf.compat.v1.Session(config=session_conf)
                with self.model.as_default(): 
                    saver = tf.compat.v1.train.import_meta_graph("{}.meta".format(self.checkpoint_file))
                    saver.restore(self.model, self.checkpoint_file) 
   
  def test_step(self,x, emb_mode):
    p = 1.0
    if emb_mode == 1: 
        feed_dict = {
            self.input_x_char_seq: x[0],
            self.dropout_keep_prob: p}  
    elif emb_mode == 2: 
        feed_dict = {
            self.input_x_word: x[0],
            self.dropout_keep_prob: p}
    elif emb_mode == 3: 
        feed_dict = {
            self.input_x_char_seq: x[0],
            self.input_x_word: x[1],
            self.dropout_keep_prob: p}
    elif emb_mode == 4: 
        feed_dict = {
            self.input_x_word: x[0],
            self.input_x_char: x[1],
            self.input_x_char_pad_idx: x[2],
            self.dropout_keep_prob: p}
    elif emb_mode == 5:  
        feed_dict = {
            self.input_x_char_seq: x[0],
            self.input_x_word: x[1],
            self.input_x_char: x[2],
            self.input_x_char_pad_idx: x[3],
            self.dropout_keep_prob: p}
    preds, s = self.model.run([self.predictions, self.scores], feed_dict)
    return preds, s

    
  def __call__(self, urls):
                x, word_reverse_dict = get_word_vocab(urls, self.max_len_words) 
                word_x = get_words(x, word_reverse_dict, self.delimit_mode, urls) 
                ngram_dict = pickle.load(open(self.subword_dict_dir, "rb")) 
                print("Size of subword vocabulary (train): {}".format(len(ngram_dict)))
                word_dict = pickle.load(open(self.word_dict_dir, "rb"))
                print("size of word vocabulary (train): {}".format(len(word_dict)))
                ngramed_id_x, worded_id_x = ngram_id_x_from_dict(word_x, self.max_len_subwords, ngram_dict, word_dict) 
                chars_dict = pickle.load(open(self.char_dict_dir, "rb"))          
                chared_id_x = char_id_x(urls, chars_dict, self.max_len_chars)  
                if  self.emb_mode in [1, 3, 5]: 
                            self.input_x_char_seq = self.graph.get_operation_by_name("input_x_char_seq").outputs[0]
                if self.emb_mode in [2, 3, 4, 5]:
                            self.input_x_word = self.graph.get_operation_by_name("input_x_word").outputs[0]
                if self.emb_mode in [4, 5]:
                    self.input_x_char = self.graph.get_operation_by_name("input_x_char").outputs[0]
                    self.input_x_char_pad_idx = self.graph.get_operation_by_name("input_x_char_pad_idx").outputs[0]
                self.dropout_keep_prob = self.graph.get_operation_by_name("dropout_keep_prob").outputs[0] 
        
                self.predictions = self.graph.get_operation_by_name("output/predictions").outputs[0]
                self.scores = self.graph.get_operation_by_name("output/scores").outputs[0]
                
                if self.emb_mode == 1: 
                    batches = batch_iter(list(chared_id_x), self.batch_size, 1, shuffle=False) 
                elif self.emb_mode == 2: 
                    batches = batch_iter(list(worded_id_x), self.batch_size, 1, shuffle=False) 
                elif self.emb_mode == 3: 
                    batches = batch_iter(list(zip(chared_id_x, worded_id_x)), self.batch_size, 1, shuffle=False)
                elif self.emb_mode == 4: 
                    batches = batch_iter(list(zip(ngramed_id_x, worded_id_x)), self.batch_size, 1, shuffle=False)
                elif self.emb_mode == 5: 
                    batches = batch_iter(list(zip(ngramed_id_x, worded_id_x, chared_id_x)), self.batch_size, 1, shuffle=False)    
                
                all_predictions = []
                all_scores = []
                nb_batches = int(len(urls) / self.batch_size)
                if (len(urls) % self.batch_size) != 0:
                  nb_batches += 1 
                print("Number of batches in total: {}".format(nb_batches))
                it = tqdm(range(nb_batches), desc="emb_mode {} delimit_mode {} test_size {}".format(self.emb_mode, self.delimit_mode, len(urls)), ncols=0)
                for idx in it:
                #for batch in batches:
                    batch = next(batches)
        
                    if self.emb_mode == 1: 
                        x_char_seq = batch 
                    elif self.emb_mode == 2: 
                        x_word = batch 
                    elif self.emb_mode == 3: 
                        x_char_seq, x_word = zip(*batch) 
                    elif self.emb_mode== 4: 
                        x_char, x_word = zip(*batch)
                    elif self.emb_mode == 5: 
                        x_char, x_word, x_char_seq = zip(*batch)            

                    x_batch = []    
                    if self.emb_mode in[1, 3, 5]: 
                        x_char_seq = pad_seq_in_word(x_char_seq, self.max_len_chars) 
                        x_batch.append(x_char_seq)
                    if self.emb_mode in [2, 3, 4, 5]:
                        x_word = pad_seq_in_word(x_word, self.max_len_words) 
                        x_batch.append(x_word)
                    if self.emb_mode in [4, 5]:
                        x_char, x_char_pad_idx = pad_seq(x_char, self.max_len_words, self.max_len_subwords, self.emb_dim)
                        x_batch.extend([x_char, x_char_pad_idx])
                    
                    batch_predictions, batch_scores = self.test_step(x_batch, self.emb_mode)     
                    print("prediction",batch_predictions)  
                    print("Score",batch_scores)     
                    all_predictions = np.concatenate([all_predictions, batch_predictions]) 
                    all_scores.extend(batch_scores) 
        
                    it.set_postfix()
                    
                    
                    print("Predictions", all_predictions)
                    softmax_scores = [softmax(i) for i in all_scores]
                    return softmax_scores
           #save_test_result(urls,labels, all_predictions, all_scores,atype,FLAGS["log.output_dir"]) 


In [9]:
from sklearn.utils import shuffle
from utils import *

In [20]:
# -*- coding: utf-8 -*-
"""
Created on Thu Aug 18 13:23:01 2022

@author: bushra
"""
import pickle 
import time 
from tqdm import tqdm
import argparse
import numpy as np 
import pickle 
import tensorflow as tf 
from tflearn.data_utils import to_categorical, pad_sequences
import pandas as pd
import csv
from sklearn.utils import shuffle
from utils import *
#tf.compat.v1.disable_v2_behavior()
from textattack.models.wrappers import ModelWrapper

def softmax(x): 
    e_x = np.exp(x - np.max(x))
    return e_x / e_x.sum() 
######################## EVALUATION ########################### 
class result():
  def __init__(self,configuration):
    self.outputdir="/content/gdrive/My Drive/TDSC_Additional_Experiments/URLNet-master/runs/10000/"+str(configuration)+"/"
    self.max_len_words = 200
    self.max_len_chars = 200
    self.max_len_subwords = 20
    self.data_dir='train_10000.txt'
    self.delimit_mode=1
    self.subword_dict_dir=self.outputdir+"subwords_dict.p"
    self.word_dict_dir=self.outputdir+"words_dict.p"
    self.char_dict_dir=self.outputdir+"chars_dict.p"
    # model args 
    self.emb_dim = 32
    self.emb_mode = configuration 
    #help="1: charCNN, 2: wordCNN, 3: char + wordCNN, 4: char-level wordCNN, 5: char + char-level wordCNN (default: {})".format(default_emb_mode))
    self.batch_size = 1
    self.checkpoint_dir=self.outputdir+"checkpoints/"
    self.checkpoint_file = tf.compat.v1.train.latest_checkpoint(self.checkpoint_dir)
    
    self.graph = tf.compat.v1.Graph() 
    with self.graph.as_default(): 
                session_conf = tf.compat.v1.ConfigProto(allow_soft_placement=True, log_device_placement=False)
                session_conf.gpu_options.allow_growth=True 
                self.model = tf.compat.v1.Session(config=session_conf)
                with self.model.as_default(): 
                    saver = tf.compat.v1.train.import_meta_graph("{}.meta".format(self.checkpoint_file))
                    saver.restore(self.model, self.checkpoint_file) 
   
  def test_step(self,x, emb_mode):
    p = 1.0
    if emb_mode == 1: 
        feed_dict = {
            self.input_x_char_seq: x[0],
            self.dropout_keep_prob: p}  
    elif emb_mode == 2: 
        feed_dict = {
            self.input_x_word: x[0],
            self.dropout_keep_prob: p}
    elif emb_mode == 3:
        print("here I am") 
        feed_dict = {
            self.input_x_char_seq: x[0],
            self.input_x_word: x[1],
            self.dropout_keep_prob: p}
    elif emb_mode == 4: 
        feed_dict = {
            self.input_x_word: x[0],
            self.input_x_char: x[1],
            self.input_x_char_pad_idx: x[2],
            self.dropout_keep_prob: p}
    elif emb_mode == 5:  
        feed_dict = {
            self.input_x_char_seq: x[0],
            self.input_x_word: x[1],
            self.input_x_char: x[2],
            self.input_x_char_pad_idx: x[3],
            self.dropout_keep_prob: p}
    preds, s = self.model.run([self.predictions, self.scores], feed_dict)
    
    return preds, s

    
  def predict(self, urls):
                x, word_reverse_dict = get_word_vocab(urls, self.max_len_words) 
                word_x = get_words(x, word_reverse_dict, self.delimit_mode, urls) 
                ngram_dict = pickle.load(open(self.subword_dict_dir, "rb")) 
                print("Size of subword vocabulary (train): {}".format(len(ngram_dict)))
                word_dict = pickle.load(open(self.word_dict_dir, "rb"))
                print("size of word vocabulary (train): {}".format(len(word_dict)))
                ngramed_id_x, worded_id_x = ngram_id_x_from_dict(word_x, self.max_len_subwords, ngram_dict, word_dict) 
                chars_dict = pickle.load(open(self.char_dict_dir, "rb"))          
                chared_id_x = char_id_x(urls, chars_dict, self.max_len_chars)  
                if  self.emb_mode in [1, 3, 5]: 
                            self.input_x_char_seq = self.graph.get_operation_by_name("input_x_char_seq").outputs[0]
                if self.emb_mode in [2, 3, 4, 5]:
                            self.input_x_word = self.graph.get_operation_by_name("input_x_word").outputs[0]
                if self.emb_mode in [4, 5]:
                    self.input_x_char = self.graph.get_operation_by_name("input_x_char").outputs[0]
                    self.input_x_char_pad_idx = self.graph.get_operation_by_name("input_x_char_pad_idx").outputs[0]
                self.dropout_keep_prob = self.graph.get_operation_by_name("dropout_keep_prob").outputs[0] 
        
                self.predictions = self.graph.get_operation_by_name("output/predictions").outputs[0]
                self.scores = self.graph.get_operation_by_name("output/scores").outputs[0]
                
                if self.emb_mode == 1: 
                    batches = batch_iter(list(chared_id_x), self.batch_size, 1, shuffle=False) 
                elif self.emb_mode == 2: 
                    batches = batch_iter(list(worded_id_x), self.batch_size, 1, shuffle=False) 
                elif self.emb_mode == 3: 
                    batches = batch_iter(list(zip(chared_id_x, worded_id_x)), self.batch_size, 1, shuffle=False)
                elif self.emb_mode == 4: 
                    batches = batch_iter(list(zip(ngramed_id_x, worded_id_x)), self.batch_size, 1, shuffle=False)
                elif self.emb_mode == 5: 
                    batches = batch_iter(list(zip(ngramed_id_x, worded_id_x, chared_id_x)), self.batch_size, 1, shuffle=False)    
                
                all_predictions = []
                all_scores = []
                nb_batches = int(len(urls) / self.batch_size)
                if (len(urls) % self.batch_size) != 0:
                  nb_batches += 1 
                print("Number of batches in total: {}".format(nb_batches))
                it = tqdm(range(nb_batches), desc="emb_mode {} delimit_mode {} test_size {}".format(self.emb_mode, self.delimit_mode, len(urls)), ncols=0)
                for idx in it:
                #for batch in batches:
                    batch = next(batches)
        
                    if self.emb_mode == 1: 
                        x_char_seq = batch 
                    elif self.emb_mode == 2: 
                        x_word = batch 
                    elif self.emb_mode == 3: 
                        x_char_seq, x_word = zip(*batch) 
                    elif self.emb_mode== 4: 
                        x_char, x_word = zip(*batch)
                    elif self.emb_mode == 5: 
                        x_char, x_word, x_char_seq = zip(*batch)            

                    x_batch = []    
                    if self.emb_mode in[1, 3, 5]: 
                        x_char_seq = pad_seq_in_word(x_char_seq, self.max_len_chars) 
                        x_batch.append(x_char_seq)
                    if self.emb_mode in [2, 3, 4, 5]:
                        x_word = pad_seq_in_word(x_word, self.max_len_words) 
                        x_batch.append(x_word)
                    if self.emb_mode in [4, 5]:
                        x_char, x_char_pad_idx = pad_seq(x_char, self.max_len_words, self.max_len_subwords, self.emb_dim)
                        x_batch.extend([x_char, x_char_pad_idx])
                    
                    batch_predictions, batch_scores = self.test_step(x_batch, self.emb_mode)     
                    print("prediction",batch_predictions)  
                    print("Score",batch_scores)     
                    all_predictions = np.concatenate([all_predictions, batch_predictions]) 
                    all_scores.extend(batch_scores) 
        
                    it.set_postfix()
                    
                    
                    print("Predictions", all_predictions)
                    softmax_scores = [softmax(i) for i in all_scores]
                    return softmax_scores
           #save_test_result(urls,labels, all_predictions, all_scores,atype,FLAGS["log.output_dir"]) 


In [21]:
r=result(3)
r.predict(['http://www.netflix.com'])

1
1
YES
Size of word vocabulary: 204354
Size of subword vocabulary (train): 389
size of word vocabulary (train): 143127
Index of <UNKNOWN> word: 91599
Processing url #0
Number of batches in total: 1


emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:00<?, ?it/s]

here I am


/content/gdrive/My Drive/TDSC_Additional_Experiments/URLNet-master/utils.py:382: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  data = np.array(data)
emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:01<?, ?it/s]

prediction [0]
Score [[ 1.4140426 -3.0852878]]
Predictions [0.]


[array([0.9890058 , 0.01099422], dtype=float32)]

In [22]:
r=result(5)
r.predict(['https://ir.netflix.com'])

1
1
YES
Size of word vocabulary: 204354
Size of subword vocabulary (train): 389
size of word vocabulary (train): 143127
Index of <UNKNOWN> word: 91599
Processing url #0
Number of batches in total: 1


emb_mode 5 delimit_mode 1 test_size 1:   0% 0/1 [00:00<?, ?it/s]

prediction [1]
Score [[-7.557425   1.8590076]]
Predictions [1.]


[array([8.1369195e-05, 9.9991858e-01], dtype=float32)]

In [23]:
import textattack
import codecs,tldextract
codecs.register_error("strict", codecs.ignore_errors)
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'DeepWordBug_URLNET(Char_WORD).csv'
model = CustomTensorFlowModelWrapperURLNET(3)
attack = textattack.attack_recipes.DeepWordBugGao2018.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

textattack: Unknown if model of class <class 'tensorflow.python.client.session.Session'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1
1
YES
Size of word vocabulary: 204354
Size of subword vocabulary (train): 389
size of word vocabulary (train): 143127
Index of <UNKNOWN> word: 91599
Processing url #0
Number of batches in total: 1


emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:00<?, ?it/s]


KeyboardInterrupt: ignored

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'Pruthi2019_URLNET(Char_WORD).csv'
model = CustomTensorFlowModelWrapperURLNET(3)

attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.Pruthi2019.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

In [13]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'PWWS_URLNET(Char_WORD).csv'
model = CustomTensorFlowModelWrapperURLNET(3)
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.PWWSRen2019.build(model)
AdversarialFile=filename

adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
textattack: Unknown if model of class <class 'tensorflow.python.client.session.Session'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1
1
YES
Size of word vocabulary: 204354
Size of subword vocabulary (train): 389
size of word vocabulary (train): 143127
Index of <UNKNOWN> word: 91599
Processing url #0
Number of batches in total: 1


emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:00<?, ?it/s]/content/gdrive/MyDrive/TDSC_Additional_Experiments/URLNet-master/utils.py:382: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  data = np.array(data)
emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:01<?, ?it/s]

prediction [1]
Score [[-1.8615282  2.557327 ]]
Predictions [1.]
['0', 'http://ir.netflix.com/', '0.9880954027175903', '1', 'http://ir.netflix.com/', '0.9880954027175903', '1', 'SKIPPED', 'True', 'False', 'False']
1
1
YES



/usr/local/lib/python3.7/dist-packages/textattack/goal_functions/classification/classification_goal_function.py:26: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at  ../torch/csrc/utils/tensor_new.cpp:201.)
  scores = torch.tensor(scores)


...

emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:00<?, ?it/s]

prediction [1]
Score [[-0.28619528  0.6869318 ]]
Predictions [1.]
['1079', 'https://www.chase.com/personal/mortgage/home-mortgage', '0.7257423400878906', '1', 'https://www.chase.com/personal/mortgage/home-mortgage', '0.7257423400878906', '1', 'SKIPPED', 'True', 'False', 'False']
1
1
YES


Size of word vocabulary: 204354
Size of subword vocabulary (train): 389
size of word vocabulary (train): 143127
Index of <UNKNOWN> word: 91599
Processing url #0
Number of batches in total: 1


emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:00<?, ?it/s]

prediction [1]
Score [[-2.152077   3.1552384]]
Predictions [1.]
['1080', 'https://www.chase.com/personal/home-equity#main', '0.9950692057609558', '1', 'https://www.chase.com/personal/home-equity#main', '0.9950692057609558', '1', 'SKIPPED', 'True', 'False', 'False']


###AttackTEXTBUGGGER

In [18]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'TEXTBUGGER_URLNET(Char_WORD).csv'
model = CustomTensorFlowModelWrapperURLNET(3)
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.TextBuggerLi2018.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

textattack: Unknown if model of class <class 'tensorflow.python.client.session.Session'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1
1
YES
Size of word vocabulary: 204354
Size of subword vocabulary (train): 389
size of word vocabulary (train): 143127
Index of <UNKNOWN> word: 91599
Processing url #0
Number of batches in total: 1


emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:00<?, ?it/s]/content/gdrive/MyDrive/TDSC_Additional_Experiments/URLNet-master/utils.py:382: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  data = np.array(data)
emb_mode 3 delimit_mode 1 test_size 1:   0% 0/1 [00:01<?, ?it/s]

prediction [1]
Score [[-1.8615282  2.557327 ]]
Predictions [1.]
['0', 'http://ir.netflix.com/', '0.9880954027175903', '1', 'http://ir.netflix.com/', '0.9880954027175903', '1', 'SKIPPED', 'True', 'False', 'False']
1
1
YES



/usr/local/lib/python3.7/dist-packages/textattack/goal_functions/classification/classification_goal_function.py:26: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at  ../torch/csrc/utils/tensor_new.cpp:201.)
  scores = torch.tensor(scores)


...

prediction [0]
Score [[ 1.4140426 -3.0852878]]
Predictions [0.]
4
4
YES


Size of word vocabulary: 204354
Size of subword vocabulary (train): 389
size of word vocabulary (train): 143127
Index of <UNKNOWN> word: 91599
Processing url #0
Number of batches in total: 1


emb_mode 3 delimit_mode 1 test_size 4:   0% 0/1 [00:01<?, ?it/s]

prediction [0 1 0 0]
Score [[ 0.66151905 -1.1434548 ]
 [-1.413938    2.075821  ]
 [ 1.8450279  -4.2888346 ]
 [ 0.31237215 -1.6515944 ]]
Predictions [0. 1. 0. 0.]


AttributeError: ignored

#LSTM CHAR

# New Section

In [22]:
import numpy as np
import tensorflow as tf
from keras import backend as K


def recall(y_true, y_pred):
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
    recall_keras = true_positives / (possible_positives + K.epsilon())
    return recall_keras


def precision(y_true, y_pred):
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
    precision_keras = true_positives / (predicted_positives + K.epsilon())
    return precision_keras


def specificity(y_true, y_pred):
    tn = K.sum(K.round(K.clip((1 - y_true) * (1 - y_pred), 0, 1)))
    fp = K.sum(K.round(K.clip((1 - y_true) * y_pred, 0, 1)))
    return tn / (tn + fp + K.epsilon())


def negative_predictive_value(y_true, y_pred):
    tn = K.sum(K.round(K.clip((1 - y_true) * (1 - y_pred), 0, 1)))
    fn = K.sum(K.round(K.clip(y_true * (1 - y_pred), 0, 1)))
    return tn / (tn + fn + K.epsilon())


def f1(y_true, y_pred):
    p = precision(y_true, y_pred)
    r = recall(y_true, y_pred)
    return 2 * ((p * r) / (p + r + K.epsilon()))


def fbeta(y_true, y_pred, beta=2):
    y_pred = K.clip(y_pred, 0, 1)

    tp = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)), axis=1)
    fp = K.sum(K.round(K.clip(y_pred - y_true, 0, 1)), axis=1)
    fn = K.sum(K.round(K.clip(y_true - y_pred, 0, 1)), axis=1)

    p = tp / (tp + fp + K.epsilon())
    r = tp / (tp + fn + K.epsilon())

    num = (1 + beta ** 2) * (p * r)
    den = (beta ** 2 * p + r + K.epsilon())
    return K.mean(num / den)


def matthews_correlation_coefficient(y_true, y_pred):
    tp = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    tn = K.sum(K.round(K.clip((1 - y_true) * (1 - y_pred), 0, 1)))
    fp = K.sum(K.round(K.clip((1 - y_true) * y_pred, 0, 1)))
    fn = K.sum(K.round(K.clip(y_true * (1 - y_pred), 0, 1)))

    num = tp * tn - fp * fn
    den = (tp + fp) * (tp + fn) * (tn + fp) * (tn + fn)
    return num / K.sqrt(den + K.epsilon())


def equal_error_rate(y_true, y_pred):
    n_imp = tf.count_nonzero(tf.equal(y_true, 0), dtype=tf.float32) + tf.constant(K.epsilon())
    n_gen = tf.count_nonzero(tf.equal(y_true, 1), dtype=tf.float32) + tf.constant(K.epsilon())

    scores_imp = tf.boolean_mask(y_pred, tf.equal(y_true, 0))
    scores_gen = tf.boolean_mask(y_pred, tf.equal(y_true, 1))

    loop_vars = (tf.constant(0.0), tf.constant(1.0), tf.constant(0.0))
    cond = lambda t, fpr, fnr: tf.greater_equal(fpr, fnr)
    body = lambda t, fpr, fnr: (
        t + 0.001,
        tf.divide(tf.count_nonzero(tf.greater_equal(scores_imp, t), dtype=tf.float32), n_imp),
        tf.divide(tf.count_nonzero(tf.less(scores_gen, t), dtype=tf.float32), n_gen)
    )
    t, fpr, fnr = tf.while_loop(cond, body, loop_vars, back_prop=False)
    eer = (fpr + fnr) / 2

    return eer

In [15]:
from textattack.models.wrappers import ModelWrapper
import tensorflow as tf
from keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
self.model = tf.keras.models.load_model('/content/gdrive/My Drive/TDSC_Additional_Experiments/Orginal_LSTM_CHAR/Finalmodel.hdf5',custom_objects={"matthews_correlation_coefficient": matthews_correlation_coefficient})
        
import pickle
class CustomTokenizerLSTM:
    
    def __init__(self):
      file_name = '/content/gdrive/My Drive/TDSC_Additional_Experiments/Orginal_LSTM_CHAR/tokenizer_lstm.pkl'
        # save
      self.tokenizer=pickle.load(open(file_name, "rb"))
      self.maxlen=128
           
    def encode(self, strings):
        Testsequences = self.tokenizer.texts_to_sequences(strings)
        testingdata=pad_sequences(Testsequences, maxlen=self.maxlen)
        return testingdata

class CustomTensorFlowModelWrapperLSTM(ModelWrapper):
    def __init__(self):
        self.tokenizer=CustomTokenizerLSTM()
        self.model = tf.keras.models.load_model('/content/gdrive/My Drive/TDSC_Additional_Experiments/Orginal_LSTM_CHAR/Finalmodel.hdf5',custom_objects={"matthews_correlation_coefficient": matthews_correlation_coefficient})
          
    def __call__(self, testurls):
        """
        Score a list of strings, returning a list [[string,score],...]
        """
        
        input_data = self.tokenizer.encode(testurls)
        result =self.model.predict(input_data)
        predictions=[]
        for i in range(len(testurls)): 
                predlabel=[0,0]
                if(result[i]>=0.5):
                  predlabel[1]=float(result[i])
                  predlabel[0]=float(1-result[i])
                else:
                  predlabel[1]=float(result[i])
                  predlabel[0]=float(1-result[i])
                # print(testurls[i],"  ",predlabel)
                predictions.append(np.array(predlabel))

           
        return predictions

        


In [17]:
import textattack
import csv
import codecs,tldextract
codecs.register_error("strict", codecs.ignore_errors)
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'TEXTFOOLER_LSTM.csv'
model = CustomTensorFlowModelWrapperLSTM()
tokenizer=CustomTokenizerLSTM()
attack = textattack.attack_recipes.TextFoolerJin2019.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

textattack: Unknown if model of class <class 'keras.engine.sequential.Sequential'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1/1 [==============================] - 0s 127ms/step


/usr/local/lib/python3.7/dist-packages/textattack/goal_functions/classification/classification_goal_function.py:26: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at  ../torch/csrc/utils/tensor_new.cpp:201.)
  scores = torch.tensor(scores)


1/1 [==============================] - 0s 118ms/step
['0', 'http://ir.netflix.com/', '0.0018892884254455566', '0', 'www://mayday.netflix.kom/', '0.36373579502105713', '0', 'FAILED', 'False', 'True', 'True']
1/1 [==============================] - 0s 134ms/step
['1', 'http://www.netflix.com', '4.1544437408447266e-05', '0', 'http://sss.netflix.coms', '0.016726136207580566', '0', 'FAILED', 'True', 'True', 'True']
1/1 [==============================] - 0s 135ms/step
['2', 'http://www.netflix.com/', '0.00015407800674438477', '0', 'http://sss.netflix.com/', '0.017604172229766846', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 123ms/step
['3', 'http://www.netflix.com/au/', '0.024740934371948242', '0', 'http://sss.netflix.com/ua/', '0.06928437948226929', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 133ms/step
['4', 'http://www.netflix.com/login', '0.9601097106933594', '1', 'http://www.netflix.com/login', '0.9601097106933

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'Pruthi2019_LSTM.csv'
model = CustomTensorFlowModelWrapperLSTM()
tokenizer=CustomTokenizerLSTM()
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.Pruthi2019.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'PWWS_LSTM.csv'
model = CustomTensorFlowModelWrapperLSTM()
tokenizer=CustomTokenizerLSTM()
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.PWWSRen2019.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
textattack: Unknown if model of class <class 'keras.engine.sequential.Sequential'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1/1 [==============================] - 0s 160ms/step
['0', 'http://ir.netflix.com/', '0.0018892884254455566', '0', 'http://iridium.netflix.com/', '0.0023611783981323242', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 179ms/step
['1', 'http://netflix.com', '0.011776387691497803', '0', 'http://netflix.com', '0.011776387691497803', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 169ms/step
['2', 'http://netflix.com/', '0.012131989002227783', '0', 'http://netflix.com/', '0.012131989002227783', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 177ms/step
['3', 'http://netflix.com/au/', '0.8856393098831177', '1', 'http://netflix.com/au/', '0.8856393098831177', '1', 'SKIPPED', 'True', 'False', 'False']
1/1 [==============================] - 0s 182ms/step
['4', 'http://netflix.com/login', '0.9958933591842651', '1', 'http://netflix.com/login', '0.9958933591842651', '1', 'SKIPPED', 'True', 'F

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'Pruthi2019_LSTM.csv'
model = CustomTensorFlowModelWrapperLSTM()
tokenizer=CustomTokenizerLSTM()
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.Pruthi2019.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status','domainchanged','tldchanged'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

In [ ]:
import textattack
path='/content/gdrive/My Drive/TDSC_Additional_Experiments/'
dataset = test_data()
filename=path+'TEXTBUGGER_LSTM.csv'
model = CustomTensorFlowModelWrapperLSTM()
tokenizer=CustomTokenizerLSTM()
attack_args = textattack.AttackArgs(num_examples=100, log_to_csv=filename, checkpoint_interval=1, checkpoint_dir="checkpoints", disable_stdout=True)
attack = textattack.attack_recipes.TextBuggerLi2018.build(model)
AdversarialFile=filename
adv=open(AdversarialFile, 'w' ,encoding='utf-8',newline='')
ad= csv.writer(adv)
ad.writerow(['id','originalexample','originalscore','originallabel','Advexample','Advscore','AdvLabel','Result','status'])
count=1
Failed=0
for i, example, label in dataset:
    
    result = attack.attack(example,label)
    
    if(result is not None):
          valid='False'
          curl=result.perturbed_text()
          
          if((is_valid_uri(curl))==True and validators.url(curl)==True ):
            valid='True'
          goalpassed=(result.goal_function_result_str())
          goal="SUCCESS"
          if('SKIPPED' in goalpassed):
                 goal='SKIPPED'
          elif('FAILED' in goalpassed):
                 goal='FAILED'
          domainchange='True'
          tldchange='True'
          [orgsld,orgdomain,orgtld]=tldextract.extract(result.original_text())
          [advld,advdomain,advtld]=tldextract.extract(result.perturbed_text())
          if(orgdomain.lower()==advdomain.lower()):
            domainchange='False'
          if(orgtld.lower()==advtld.lower()):
            tldchange='False'
          row=[str(i),result.original_text(),str(result.original_result.score),str(result.original_result.output),result.perturbed_text(),str(result.perturbed_result.score),str(result.perturbed_result.output),goal,valid,domainchange,tldchange]
          print(row)
          ad.writerow(row)
adv.close()

textattack: Downloading https://textattack.s3.amazonaws.com/word_embeddings/paragramcf.
100%|██████████| 481M/481M [00:10<00:00, 46.4MB/s]
textattack: Unzipping file /root/.cache/textattack/tmp8vmfgp2_.zip to /root/.cache/textattack/word_embeddings/paragramcf.
textattack: Successfully saved word_embeddings/paragramcf to cache.
textattack: Unknown if model of class <class 'keras.engine.sequential.Sequential'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


1/1 [==============================] - 0s 157ms/step
['0', 'http://ir.netflix.com/', '0.0018892884254455566', '0', 'http://ir.netflix.com/', '0.0018892884254455566', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 160ms/step
['1', 'http://netflix.com', '0.011776387691497803', '0', 'http://netflix.com', '0.011776387691497803', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 156ms/step
['2', 'http://netflix.com/', '0.012131989002227783', '0', 'http://netflix.com/', '0.012131989002227783', '0', 'FAILED', 'True', 'False', 'False']
1/1 [==============================] - 0s 179ms/step
['3', 'http://netflix.com/au/', '0.8856393098831177', '1', 'http://netflix.com/au/', '0.8856393098831177', '1', 'SKIPPED', 'True', 'False', 'False']
1/1 [==============================] - 0s 178ms/step
['4', 'http://netflix.com/login', '0.9958933591842651', '1', 'http://netflix.com/login', '0.9958933591842651', '1', 'SKIPPED', 'True', 'False'

#Robustnesss Evaluation

In [19]:
!git clone https://github.com/KaidiXu/auto_LiRPA


Cloning into 'auto_LiRPA'...
remote: Enumerating objects: 507, done.
remote: Counting objects: 100% (128/128), done.
remote: Compressing objects: 100% (65/65), done.
remote: Total 507 (delta 99), reused 63 (delta 63), pack-reused 379
Receiving objects: 100% (507/507), 4.73 MiB | 13.04 MiB/s, done.
Resolving deltas: 100% (265/265), done.
python3: can't open file 'setup.py': [Errno 2] No such file or directory


In [20]:
import os
os.chdir(f'/content/auto_LiRPA')

In [ ]:
!python setup.py install


In [28]:
import os
import torch
import torch.nn as nn
import torchvision
from auto_LiRPA import BoundedModule, BoundedTensor
from auto_LiRPA.perturbations import PerturbationLpNorm

class Flatten(nn.Module):
    def forward(self, x):
        return x.view(x.size(0), -1)


In [30]:
def lstm(tokenizer):
      num_chars = len(tokenizer.word_index)+1
      embedding_vector_length = 128

      # Create model for training.
      model = Sequential()
      model.add(Embedding(num_chars, embedding_vector_length, input_length=maxlen))
      model.add(Bidirectional(LSTM(128, dropout=0.2, recurrent_dropout=0.2, return_sequences=True)))
      model.add(Bidirectional(LSTM(64, dropout=0.2, recurrent_dropout=0.2)))
      model.add(Dense(1, activation='sigmoid'))
      model.summary()
      model.compile(optimizer='adam',
                  loss='binary_crossentropy',
                  metrics=[matthews_correlation_coefficient])
      return model

In [32]:
from auto_LiRPA import BoundedModule, BoundedTensor, PerturbationLpNorm
from textattack.models.wrappers import ModelWrapper
import tensorflow as tf
from keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
# Optionally, load the pretrained weights.
model = tf.keras.models.load_model('/content/gdrive/My Drive/TDSC_Additional_Experiments/Orginal_LSTM_CHAR/Finalmodel.hdf5',custom_objects={"matthews_correlation_coefficient": matthews_correlation_coefficient})
test_data=pd.read_csv(path+'popularseedurlsbase.csv',encoding="utf-8")
data_test=test_data['url']
my_input = data_test
# Wrap the model with auto_LiRPA.
model = BoundedModule(model, my_input)
# Define perturbation. Here we add Linf perturbation to input data.
ptb = PerturbationLpNorm(norm=np.inf, eps=0.1)
# Make the input a BoundedTensor with the pre-defined perturbation.
my_input = BoundedTensor(my_input, ptb)
# Regular forward propagation using BoundedTensor works as usual.
prediction = model(my_input)
# Compute LiRPA bounds using the backward mode bound propagation (IBP).
lb, ub = model.compute_bounds(x=(my_input,), method="IBP")

AttributeError: ignored